<a href="https://colab.research.google.com/github/jiaojx1987/DataScience/blob/main/Showcase/customer_segmentation/Customer_Segmentation_ShowCase.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Importing Libraries</P>



In [ ]:
# importing the libraries
import numpy as np
import pandas as pd
import datetime
import matplotlib
import matplotlib.pyplot as plt
from matplotlib import colors
import seaborn as sns
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from yellowbrick.cluster import KElbowVisualizer
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt, numpy as np
from mpl_toolkits.mplot3d import Axes3D
from sklearn.cluster import AgglomerativeClustering
from matplotlib.colors import ListedColormap
from sklearn import metrics
import warnings
import sys
if not sys.warnoptions:
    warnings.simplefilter("ignore")
np.random.seed(9567)

pd.options.mode.copy_on_write = True

Let's loading the data and show some examples in the data.

In [ ]:
# loading the data
file_link = "https://raw.githubusercontent.com/jiaojx1987/DataScience/main/Showcase/customer_segmentation/marketing_campaign.CSV"
data = pd.read_csv(file_link)
data.head()

ID  Year_Birth   Education Marital_Status   Income  Kidhome  Teenhome  \
0  5524        1957  Graduation         Single  58138.0        0         0   
1  2174        1954  Graduation         Single  46344.0        1         1   
2  4141        1965  Graduation       Together  71613.0        0         0   
3  6182        1984  Graduation       Together  26646.0        1         0   
4  5324        1981         PhD        Married  58293.0        1         0   

  Dt_Customer  Recency  MntWines  ...  NumCatalogPurchases  NumStorePurchases  \
0  04-09-2012       58       635  ...                   10                  4   
1  08-03-2014       38        11  ...                    1                  2   
2  21-08-2013       26       426  ...                    2                 10   
3  10-02-2014       26        11  ...                    0                  4   
4  19-01-2014       94       173  ...                    3                  6   

   NumWebVisitsMonth  AcceptedCmp3  AcceptedCmp4  AcceptedCmp5  AcceptedCmp1  \
0                  7             0             0             0             0   
1                  5             0             0             0             0   
2                  4             0             0             0             0   
3                  6             0             0             0             0   
4                  5             0             0             0             0   

   AcceptedCmp2  Complain  Response  
0             0         0         1  
1             0         0         0  
2             0         0         0  
3             0         0         0  
4             0         0         0  

[5 rows x 27 columns]

For more information on the attributes, click [here](https://raw.githubusercontent.com/jiaojx1987/DataScience/main/Showcase/customer_segmentation/Atrribute%20Explanation.txt).

# DATA CLEANING

First of all, let us have a look at the information in the data.

In [ ]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2240 entries, 0 to 2239
Data columns (total 27 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   ID                   2240 non-null   int64  
 1   Year_Birth           2240 non-null   int64  
 2   Education            2240 non-null   object 
 3   Marital_Status       2240 non-null   object 
 4   Income               2216 non-null   float64
 5   Kidhome              2240 non-null   int64  
 6   Teenhome             2240 non-null   int64  
 7   Dt_Customer          2240 non-null   object 
 8   Recency              2240 non-null   int64  
 9   MntWines             2240 non-null   int64  
 10  MntFruits            2240 non-null   int64  
 11  MntMeatProducts      2240 non-null   int64  
 12  MntFishProducts      2240 non-null   int64  
 13  MntSweetProducts     2240 non-null   int64  
 14  MntGoldProds         2240 non-null   int64  
 15  NumDealsPurchases    2240 non-null   i

Frome the above output, we can get the following concludions:
- there are missing values in "Income" column
- The "Dt_Customer" should be DateTime form because it is the date of customer's enrollment with the company

In [ ]:
a = data['Income'].isna().sum()
print("The total number of missing values in Income is {}".format(data["Income"].isna().sum()))

The total number of missing values in Income is 24


In [ ]:
data["Marital_Status"].unique()

array(['Single', 'Together', 'Married', 'Divorced', 'Widow', 'Alone',
       'Absurd', 'YOLO'], dtype=object)

Because the total number of missing values in Income about 1% of total, we just need remove those rows.

In [ ]:
data = data.dropna()
print("The total number of rows without missing value are: {}".format(len(data)))

The total number of rows without missing value are: 2216


In [ ]:
data["Education"].unique()

array(['Graduation', 'PhD', 'Master', 'Basic', '2n Cycle'], dtype=object)

Then, let us create some new features depend on the dataset.
- **Current_Age**: the customer's age stop by 2022.
- **Member_Lenght**: the month from customer be the member
- **N_Children**: total number of kids and teenagers in one family.
- **N_Family**: total number of a family. Depneding on the category of **Marital_Status**, we assume Married and Together indicates 2 adults and otherwise is 1 adult.
- **Total_Spend**: the total amount spend in various categories.
- **Is_Parent**: 1 if the parent lives with children, 0 otherwise.
- **Is_Graduate**: 1 if the education level is bachelor or higher, 0 otherwise.

In [ ]:

data["Current_Age"] = 2022 - data["Year_Birth"]

data["Dt_Customer"] = pd.to_datetime(data["Dt_Customer"])
data["Member_Length"] = data["Dt_Customer"].dt.month + (2022 - data["Dt_Customer"].dt.year)*12

data["N_Children"] = data["Kidhome"]+data["Teenhome"]

data["N_Family"] = data["Marital_Status"].replace({"Married":2,"Together":2,"Single":1,"Divorced":1,"Widow":1,"Alone":1,"Absurd":1,"YOLO":1})+data["N_Children"]

data["Total_Spend"] = data["NumWebPurchases"]+data["NumCatalogPurchases"]+data["NumStorePurchases"]+data["NumWebVisitsMonth"]

data["Is_Parent"] = np.where(data.N_Children>0, 1, 0)

data["Is_Graduate"] = data["Education"].replace({"Graduation":1, "PhD":1, "Master":1, "Basic":0, "2n Cycle":0})

<ipython-input-9-d080211841ea>:3: UserWarning: Parsing dates in DD/MM/YYYY format when dayfirst=False (the default) was specified. This may lead to inconsistently parsed dates! Specify a format to ensure consistent parsing.
  data["Dt_Customer"] = pd.to_datetime(data["Dt_Customer"])


Now, let have a look at those new features.

In [ ]:
data[data["Year_Birth"] < 1900]

ID  Year_Birth Education Marital_Status   Income  Kidhome  Teenhome  \
239  11004        1893  2n Cycle         Single  60182.0        0         1   
339   1150        1899       PhD       Together  83532.0        0         0   

    Dt_Customer  Recency  MntWines  ...  AcceptedCmp2  Complain  Response  \
239  2014-05-17       23         8  ...             0         0         0   
339  2013-09-26       36       755  ...             0         0         0   

     Current_Age  Member_Length  N_Children  N_Family  Total_Spend  Is_Parent  \
239          129            101           1         2            7          1   
339          123            117           0         2           15          0   

     Is_Graduate  
239            0  
339            1  

[2 rows x 34 columns]

In [ ]:
data[["Current_Age","Member_Length","N_Children","N_Family","Total_Spend","Is_Parent","Is_Graduate"]].describe()

Current_Age  Member_Length   N_Children     N_Family  Total_Spend  \
count  2216.000000    2216.000000  2216.000000  2216.000000  2216.000000   
mean     53.179603     114.175993     0.947202     2.592509    17.876354   
std      11.985554      10.060794     0.749062     0.905722     6.548176   
min      26.000000      97.000000     0.000000     1.000000     0.000000   
25%      45.000000     109.000000     0.000000     2.000000    12.000000   
50%      52.000000     114.000000     1.000000     3.000000    17.000000   
75%      63.000000     120.000000     1.000000     3.000000    23.000000   
max     129.000000     132.000000     3.000000     5.000000    38.000000   

         Is_Parent  Is_Graduate  
count  2216.000000  2216.000000  
mean      0.714350     0.885379  
std       0.451825     0.318636  
min       0.000000     0.000000  
25%       0.000000     1.000000  
50%       1.000000     1.000000  
75%       1.000000     1.000000  
max       1.000000     1.000000

Let us have a look at the broader view of the data. Let show if there are any relationship between each pairs of

In [ ]:
data.columns

Index(['ID', 'Year_Birth', 'Education', 'Marital_Status', 'Income', 'Kidhome',
       'Teenhome', 'Dt_Customer', 'Recency', 'MntWines', 'MntFruits',
       'MntMeatProducts', 'MntFishProducts', 'MntSweetProducts',
       'MntGoldProds', 'NumDealsPurchases', 'NumWebPurchases',
       'NumCatalogPurchases', 'NumStorePurchases', 'NumWebVisitsMonth',
       'AcceptedCmp3', 'AcceptedCmp4', 'AcceptedCmp5', 'AcceptedCmp1',
       'AcceptedCmp2', 'Complain', 'Response', 'Current_Age', 'Member_Length',
       'N_Children', 'N_Family', 'Total_Spend', 'Is_Parent', 'Is_Graduate'],
      dtype='object')

In [ ]:
sns.set(rc={"axes.facecolor":"#FFF9ED","figure.facecolor":"#FFF9ED"})
New_Features = ["Current_Age","Member_Length","N_Children","N_Family","Is_Parent","Is_Graduate","Total_Spend","Income"]
#pallet = ["#38B4Fb", "#9E724F", "#D6B2B2", "#B9C0C9", "#9F8A78", "#F3AB60"]
#cmap = colors.ListedColormap(pallet)
plt.figure()
#sns.pairplot(data[New_Features])
plt.show()

<Figure size 800x550 with 0 Axes>

Because the maximume of recency in the three person set is 99, we accept those three record as normal

In [ ]:
# Dropping the outliers by setting a cap on Age and Income.
data = data[data["Current_Age"]<100]
data = data[data["Income"]<600000]
print("The total number of data-points after removing the outliers are:", len(data))

The total number of data-points after removing the outliers are: 2212


In [ ]:
corrmat = data.corr()
plt.figure(figsize=(30,30))
#sns.heatmap(corrmat, annot=True, cmap=cmap, center=0)
#plt.show()

<ipython-input-15-a052b6462648>:1: FutureWarning: The default value of numeric_only in DataFrame.corr is deprecated. In a future version, it will default to False. Select only valid columns or specify the value of numeric_only to silence this warning.
  corrmat = data.corr()


<Figure size 3000x3000 with 0 Axes>

<Figure size 3000x3000 with 0 Axes>

In [ ]:
# Now we should drop some redundant features
drop_list = ["Year_Birth", "Dt_Customer", "Recency"]
data = data.drop(drop_list, axis=1)

In [ ]:
#data.columns.tolist()

# Data Preprocessing
In these section, we will
- label encoding the categorical features,
- normalizing the data with Standard Scalar,
- and create new dataframe with dimensionality reduction with PCA technical

In [ ]:
# Get list of categorical variables
s = (data.dtypes =="object")
cate_list = list(s[s].index)
print("Categorical variables in the dataset: ", cate_list)

Categorical variables in the dataset:  ['Education', 'Marital_Status']


In [ ]:
# Label encoding the object types:
label_encoder = LabelEncoder()
for i in cate_list:
  data[i] = data[[i]].apply(label_encoder.fit_transform)

In [ ]:
# Standardized the features.
scaler = StandardScaler()
scaler.fit(data)
scaled_df = pd.DataFrame(scaler.transform(data), columns=data.columns)
scaled_df.head()

ID  Education  Marital_Status    Income   Kidhome  Teenhome  \
0 -0.018837  -0.352543        0.254760  0.287105 -0.822754 -0.929699   
1 -1.050626  -0.352543        0.254760 -0.260882  1.040021  0.908097   
2 -0.444797  -0.352543        1.183144  0.913196 -0.822754 -0.929699   
3  0.183824  -0.352543        1.183144 -1.176114  1.040021 -0.929699   
4 -0.080437   1.429916       -0.673624  0.294307  1.040021 -0.929699   

   MntWines  MntFruits  MntMeatProducts  MntFishProducts  ...  AcceptedCmp2  \
0  0.977660   1.552041         1.690293         2.453472  ...     -0.117256   
1 -0.872618  -0.637461        -0.718230        -0.651004  ...     -0.117256   
2  0.357935   0.570540        -0.178542         1.339513  ...     -0.117256   
3 -0.872618  -0.561961        -0.655787        -0.504911  ...     -0.117256   
4 -0.392257   0.419540        -0.218684         0.152508  ...     -0.117256   

   Complain  Response  Current_Age  Member_Length  N_Children  N_Family  \
0  -0.09552  2.375425     1.018352       0.975728   -1.264598 -1.758359   
1  -0.09552 -0.420977     1.274785      -1.011758    1.404572  0.449070   
2  -0.09552 -0.420977     0.334530       0.180734   -1.264598 -0.654644   
3  -0.09552 -0.420977    -1.289547      -0.813009    0.069987  0.449070   
4  -0.09552 -0.420977    -1.033114      -1.707378    0.069987  0.449070   

   Total_Spend  Is_Parent  Is_Graduate  
0     1.697662  -1.581139     0.358569  
1    -1.357978   0.632456     0.358569  
2     0.933752  -1.581139     0.358569  
3    -0.899632   0.632456     0.358569  
4     0.169842   0.632456     0.358569  

[5 rows x 31 columns]

In [ ]:
# Now, let us create new dataframe with dimensionality reduction with PCA technical
# If we feed the model with an excessively large dataset, it gives rise to the problem of overfitting.
# For reduceing the dimention of the dataset, and try to keep all information, we will use PCA (Principal Component Analysis) technique.
# Let use reduce dimentions aka features to 3
pca = PCA(n_components=3)
pca.fit(scaled_df)
pca_df = pd.DataFrame(pca.transform(scaled_df),columns=["Col1", "Col2", "Col3"])
pca_df.describe().T

count          mean       std       min       25%       50%       75%  \
Col1  2212.0 -2.569775e-16  2.892050 -5.547739 -2.576283 -0.762990  2.386569   
Col2  2212.0  9.636656e-17  1.797293 -4.574237 -1.400111 -0.188323  1.292122   
Col3  2212.0  1.284887e-17  1.406645 -5.055203 -0.826891  0.072198  0.643729   

           max  
Col1  8.212203  
Col2  6.070703  
Col3  8.172785

In [ ]:
sns.pairplot(scaled_df)

In [ ]:
#x =pca_df["Col1"]
#y =pca_df["Col2"]
#z =pca_df["Col3"]
#To plot
#fig = plt.figure(figsize=(10,8))
#ax = fig.add_subplot(111, projection="3d")
#ax.scatter(x,y,z, c="maroon", marker="o" )
#ax.set_title("A 3D Projection Of Data In The Reduced Dimension")
#plt.show()